<a href="https://colab.research.google.com/github/AIkikr/voice_agent/blob/main/whisper_agents.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
!pip install -U openai openai-agents pydub

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 606.1/606.1 kB 26.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.9/98.9 kB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 128.6/128.6 kB 12.1 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 1.66.3
    Uninstalling openai-1.66.3:
      Successfully uninstalled openai-1.66.3


In [18]:
from google.colab import files
uploaded = files.upload()


Saving AIエージェントテスト.WAV to AIエージェントテスト.WAV


In [5]:
import os
import openai
from agents import Agent, Runner
from IPython.display import Audio, display
from pydub import AudioSegment

# ====================================
# 事前準備: APIキー
# ====================================
# 環境変数 OPENAI_API_KEY にセット済みとして想定
# APIキーがセットされていない場合はエラー終了
from google.colab import userdata
import os
os.environ["OPENAI_API_KEY"] = userdata.get('OPENAI_API_KEY')


!pip install openai
import openai
from openai import OpenAI
client = OpenAI()

if 'OPENAI_API_KEY' not in os.environ:
    print("ERROR: OPENAI_API_KEY is not set.")
    sys.exit(1)

# OpenAI クライアント初期化
client = OpenAI(api_key=os.environ['OPENAI_API_KEY'])



In [19]:
def speech_to_text(audio_path):
    with open(audio_path, "rb") as audio_file:
        transcription = openai.audio.transcriptions.create(
            model="gpt-4o-transcribe",
            file=audio_file
        )
    return transcription.text

# ファイル名を置き換えてください
input_audio_path = "AIエージェントテスト.WAV"
recognized_text = speech_to_text(input_audio_path)
print("🎙️ 音声からのテキスト変換結果:", recognized_text)


🎙️ 音声からのテキスト変換結果: AIエージェントは、業務の自動化や効率化を実現するための重要なツールとして注目されています。例えば、コールセンター業務では、生成AIを活用したハイブリッドオペレーションループにより、通話データからナレッジベースを自動生成し、回答精度の向上と業務効率化を実現しています。また、ゲーム開発の分野では、生成AIを活用したチャットボットが導入され、開発者がゲームエンジンに関する質問を効率的に行える環境が整備されています。さらに、金融業界では、AIエージェントが資金の流れの分析や不正取引の検出など、複雑なプロセスの自動化に役立っています。これらの事例からも分かるように、AIエージェントは、多様な業界で業務効率化やイノベーションの推進に貢献しています。


In [20]:
!pip install nest_asyncio
import nest_asyncio
nest_asyncio.apply()

# Agentを要約専門として設定
agent = Agent(
    name="JapaneseSummarizer",
    instructions="あなたは日本語のテキストを簡潔に要約する専門家です。重要なポイントを300文字以内でまとめてください。"
)

async def summarize_text(input_text):
    result = await Runner.run(agent, input_text)
    return result.final_output

import asyncio

summary_text = asyncio.run(summarize_text(recognized_text))
print("🤖 エージェントによる要約:", summary_text)


🤖 エージェントによる要約: AIエージェントは多様な業界で業務の自動化と効率化を推進する重要なツールです。コールセンターでは生成AIを用いて通話データからナレッジベースを自動生成し、回答精度と業務効率が向上しています。ゲーム開発では生成AIによるチャットボットが導入され、開発者がゲームエンジンに関する質問を素早く解決できる体制が整っています。金融業界ではAIが資金流れの分析や不正取引の検出を自動化しており、業務効率化に寄与しています。これにより、AIは各業界におけるイノベーション促進に貢献しています。


In [24]:
def text_to_speech(text, output_path):
    response = openai.audio.speech.create(
        model="gpt-4o-mini-tts",
        voice="alloy",
        input=text,
        response_format="mp3"
    )
    response.stream_to_file(output_path)

output_audio_path = "summary_response.mp3"
text_to_speech(summary_text, output_audio_path)

# Colab内で音声を再生
from IPython.display import Audio, display
display(Audio(output_audio_path, autoplay=True))


<ipython-input-24-613065508332>:8: DeprecationWarning: Due to a bug, this method doesn't actually stream the response content, `.with_streaming_response.method()` should be used instead
  response.stream_to_file(output_path)


In [ ]:
import openai
import asyncio
from openai import Agent, Runner
from IPython.display import Audio, display

# 仮のAPIキーとモデル設定
openai.api_key = "YOUR_API_KEY"

# =======================
# エージェント定義
# =======================

# 1. Router/Dispatcherエージェント
router_agent = Agent(
    name="RouterAgent",
    instructions=(
        "You receive a user request in text form. "
        "Determine which of the following tasks are needed: "
        "1) WebSearchAgent for fetching latest info from the web, "
        "2) SummarizerAgent for summarizing text, "
        "3) TranslatorAgent for translating text, "
        "4) SlideAggregatorAgent for creating or consolidating slide outlines, "
        "5) TTSAgent for speech output. "
        "Return a JSON-like structure describing which agents to call and in what order. "
        "If something is not needed, omit it. Be concise but clear."
    )
)

# 2. Web検索エージェント (仮)
web_search_agent = Agent(
    name="WebSearchAgent",
    instructions=(
        "You perform web searches and return relevant text data. "
        "Input is a query. Output is a text summary of the search results."
    )
)

# 3. Summarizerエージェント
summarizer_agent = Agent(
    name="SummarizerAgent",
    instructions=(
        "You take text input and produce a concise summary in Japanese."
    )
)

# 4. Translatorエージェント
translator_agent = Agent(
    name="TranslatorAgent",
    instructions=(
        "You translate text from Japanese to English or vice versa upon request."
    )
)

# 5. スライド取りまとめエージェント
slide_aggregator_agent = Agent(
    name="SlideAggregatorAgent",
    instructions=(
        "You take relevant text, summaries, or bullet points, "
        "and produce a coherent slide outline (in Markdown or bullet style). "
        "You can combine multiple inputs if needed."
    )
)

# 6. 音声合成エージェント
tts_agent = Agent(
    name="TTSAgent",
    instructions=(
        "You convert text into spoken Japanese. Provide a playable audio output."
    )
)

# =======================
# 音声処理の関数 (仮)
# =======================

def speech_to_text(audio_path):
    """
    仮想の音声認識API呼び出し
    """
    with open(audio_path, "rb") as audio_file:
        transcription = openai.audio.transcriptions.create(
            model="gpt-4o-transcribe",
            file=audio_file
        )
    return transcription.text

def text_to_speech(text, output_path):
    """
    仮想の音声合成API呼び出し
    """
    response = openai.audio.speech.create(
        model="gpt-4o-mini-tts",
        voice="alloy",
        input=text,
        response_format="mp3"
    )
    response.stream_to_file(output_path)

# =======================
# メインの処理フロー (例)
# =======================

async def main():
    # 1. ユーザー音声入力の取得
    input_audio_path = "input.wav"
    recognized_text = speech_to_text(input_audio_path)
    print("🎙 ユーザーの発話認識結果:\n", recognized_text)

    # 2. RouterAgentに渡して、どのエージェントをどう呼ぶかの指示を受け取る
    routing_instructions = await Runner.run(router_agent, recognized_text)
    routing_plan_str = routing_instructions.final_output
    print("🔀 RouterAgentからの指示:\n", routing_plan_str)

    # 3. RouterAgentの結果をパースし、必要なエージェントを順次呼び出す
    #   ここでは JSON 形式を仮定して単純に eval などで処理する例。
    #   実運用では安全性のため json.loads を使い、厳格にvalidateすることを推奨。
    import json
    try:
        routing_plan = json.loads(routing_plan_str)
    except:
        routing_plan = {}

    # 例: routing_plan = {
    #   "tasks": [
    #       {"agent": "WebSearchAgent", "input": "最新の技術ニュースについて"},
    #       {"agent": "SummarizerAgent", "input_key": "web_result"},
    #       {"agent": "TranslatorAgent", "input_key": "summary", "direction": "JA->EN"},
    #       {"agent": "SlideAggregatorAgent", "input_keys": ["summary", "translation"]},
    #       {"agent": "TTSAgent", "input_key": "slide_outline"}
    #   ]
    # }

    # 中間結果を格納していく辞書
    context = {"recognized_text": recognized_text}

    for task in routing_plan.get("tasks", []):
        agent_name = task.get("agent")
        if agent_name == "WebSearchAgent":
            query = task.get("input", "")
            # Web検索エージェントへの入力を実行
            web_result = await Runner.run(web_search_agent, query)
            context["web_result"] = web_result.final_output

        elif agent_name == "SummarizerAgent":
            input_key = task.get("input_key", "")
            text_to_summarize = context.get(input_key, "")
            summary_res = await Runner.run(summarizer_agent, text_to_summarize)
            context["summary"] = summary_res.final_output

        elif agent_name == "TranslatorAgent":
            input_key = task.get("input_key", "")
            direction = task.get("direction", "JA->EN")
            text_to_translate = context.get(input_key, "")
            # directionに応じて指示文を生成する簡易例
            translation_prompt = f"Translate this text ({direction}):\n{text_to_translate}"
            translation_res = await Runner.run(translator_agent, translation_prompt)
            context["translation"] = translation_res.final_output

        elif agent_name == "SlideAggregatorAgent":
            input_keys = task.get("input_keys", [])
            # 複数のテキストをまとめてスライドにする
            combined_input = ""
            for k in input_keys:
                combined_input += f"{k}:\n{context.get(k, '')}\n"
            slide_res = await Runner.run(slide_aggregator_agent, combined_input)
            context["slide_outline"] = slide_res.final_output

        elif agent_name == "TTSAgent":
            input_key = task.get("input_key", "")
            text_for_tts = context.get(input_key, "")
            output_audio_path = "response.mp3"
            text_to_speech(text_for_tts, output_audio_path)
            print("🔊 スライドまとめ音声生成が完了しました。")
            display(Audio(output_audio_path, autoplay=True))

        else:
            print(f"Unknown agent: {agent_name}")

    print("\n=== 処理完了 ===")
    print("最終的なcontext:", context)

# 実行
asyncio.run(main())


In [25]:
pip install 'openai-agents[voice]'

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.4/16.4 MB 120.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 182.3/182.3 kB 13.5 MB/s eta 0:00:00
  Attempting uninstall: websockets
    Found existing installation: websockets 14.2
    Uninstalling websockets-14.2:
      Successfully uninstalled websockets-14.2
  Attempting uninstall: numpy
    Found existing installation: numpy 2.0.2
    Uninstalling numpy-2.0.2:
      Successfully uninstalled numpy-2.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
numba 0.60.0 requires numpy<2.1,>=1.22, but you have numpy 2.2.4 which is incompatible.
tensorflow 2.18.0 requires numpy<2.1.0,>=1.26.0, but you have numpy 2.2.4 which is incompatible.
google-genai 1.5.0 requires websockets<15.0dev,>=13.0, but you have websockets 15.0.1 

In [42]:
!pip install -U librosa

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.9/60.9 kB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.5/19.5 MB 115.6 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 2.2.4
    Uninstalling numpy-2.2.4:
      Successfully uninstalled numpy-2.2.4


In [29]:
from google.colab import userdata
import os
os.environ["OPENAI_API_KEY"] = userdata.get('OPENAI_API_KEY')
os.environ["BRAVE_API_KEY"] = userdata.get('BRAVE_API_KEY')

In [72]:
!pip install langchain_openai langchain_community langgraph python-dotenv soundfile

import os
from dotenv import load_dotenv

load_dotenv()

OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")
BRAVE_API_KEY = os.getenv("BRAVE_API_KEY")

if not OPENAI_API_KEY or not BRAVE_API_KEY:
    print("⚠️ APIキーが設定されていません。 .env に OPENAI_API_KEY と BRAVE_API_KEY を記入してください。")


In [31]:
import requests
from langchain_openai import ChatOpenAI
from langchain.agents import initialize_agent, AgentType, Tool
from langchain_community.tools import BraveSearch
from typing import Optional

# 1. LLMモデルを初期化（GPT-4o-miniを仮想）
llm = ChatOpenAI(
    model="gpt-4o-mini",
    temperature=0,
    openai_api_key=OPENAI_API_KEY
)

# 2. Brave Search の設定
brave_search_tool_instance = BraveSearch.from_api_key(
    api_key=BRAVE_API_KEY,
    search_kwargs={"count": 5}  # 検索結果数
)

# 3. ツール定義
search_tool = Tool(
    name="BraveSearch",
    func=brave_search_tool_instance.run,
    description="最新情報をBrave Searchで検索します。入力はクエリ文字列。"
)

# 4. LangChain エージェントを初期化（検索ツール対応）
tools = [search_tool]
agent_executor = initialize_agent(
    tools,
    llm,
    agent=AgentType.ZERO_SHOT_REACT_DESCRIPTION,
    verbose=True,
    max_iterations=3
)

def run_search_agent(question: str) -> str:
    """Brave Search + LLMによる回答"""
    return agent_executor.run(question)


<frozen abc>:123: RuntimeWarning: coroutine 'Runner.run' was never awaited
<ipython-input-31-f85d958cc170>:29: LangChainDeprecationWarning: LangChain agents will continue to be supported, but it is recommended for new use cases to be built with LangGraph. LangGraph offers a more flexible and full-featured framework for building agents, including support for tool-calling, persistence of state, and human-in-the-loop workflows. For details, refer to the `LangGraph documentation <https://langchain-ai.github.io/langgraph/>`_ as well as guides for `Migrating from AgentExecutor <https://python.langchain.com/docs/how_to/migrate_agent/>`_ and LangGraph's `Pre-built ReAct agent <https://langchain-ai.github.io/langgraph/how-tos/create-react-agent/>`_.
  agent_executor = initialize_agent(


In [91]:
from IPython.display import Javascript, display
from google.colab import output
import base64
import uuid

recorded_audio_file = None

def save_audio(base64_str):
    global recorded_audio_file
    wav_data = base64.b64decode(base64_str)
    recorded_audio_file = f"recorded_{uuid.uuid4().hex}.wav"
    with open(recorded_audio_file, "wb") as f:
        f.write(wav_data)
    print(f"✅ 録音ファイルを保存しました: {recorded_audio_file}")

output.register_callback('notebook.save_audio', save_audio)

display(Javascript("""
var recordButton = document.createElement('button');
recordButton.textContent = 'Start Recording';
var stopButton = document.createElement('button');
stopButton.textContent = 'Stop Recording';
document.body.appendChild(document.createElement('br'));
document.body.appendChild(recordButton);
document.body.appendChild(stopButton);

var base64data = "";
let mediaRecorder;
let audioChunks = [];

recordButton.onclick = async () => {
  audioChunks = [];
  let stream = await navigator.mediaDevices.getUserMedia({ audio: true });
  mediaRecorder = new MediaRecorder(stream);
  mediaRecorder.ondataavailable = e => {
    if (e.data.size > 0) audioChunks.push(e.data);
  };
  mediaRecorder.start();
  console.log("Recording...");
};

stopButton.onclick = async () => {
  mediaRecorder.stop();
  mediaRecorder.onstop = async e => {
    const blob = new Blob(audioChunks, {'type': 'audio/wav; codecs=MS_PCM'});
    let arrayBuffer = await blob.arrayBuffer();
    let uint8Array = new Uint8Array(arrayBuffer);
    let binaryString = '';
    for (let i = 0; i < uint8Array.byteLength; i++) {
      binaryString += String.fromCharCode(uint8Array[i]);
    }
    base64data = btoa(binaryString);
    google.colab.kernel.invokeFunction('notebook.save_audio', [base64data], {});
  };
  console.log("Stopped.");
};
"""))


<IPython.core.display.Javascript object>

✅ 録音ファイルを保存しました: recorded_f405919927a04c4b89122a3d4be82097.wav


In [56]:
import librosa, soundfile as sf
import numpy as np

In [66]:
# まず、録音用スクリプトを実行して、
# グローバル変数 recorded_audio_file にファイル名が保存されることを確認してください。
# 例: "recorded_5768db4043ad464eb4c182cdb923c451.wav"

# その後、以下のコードで録音ファイルを変換します

import librosa
import soundfile as sf

def convert_audio_to_openai_format(input_path, output_path):
    audio, sr = librosa.load(input_path, sr=24000, mono=True)  # 24kHz, mono
    sf.write(output_path, audio, 24000, subtype='PCM_16')
    print(f"🔄 音声を変換しました: {output_path}")

# recorded_audio_file は録音用スクリプトで自動的に設定されるグローバル変数です。
if recorded_audio_file is None:
    print("⚠️ 録音ファイルがまだありません。まず録音を完了してください。")
else:
    converted_audio_file = "converted_audio.wav"
    convert_audio_to_openai_format(recorded_audio_file, converted_audio_file)


🔄 音声を変換しました: converted_audio.wav


<ipython-input-66-4880a7f6b0b0>:11: UserWarning: PySoundFile failed. Trying audioread instead.
  audio, sr = librosa.load(input_path, sr=24000, mono=True)  # 24kHz, mono
/usr/local/lib/python3.11/dist-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


In [67]:
import openai

def speech_to_text(file_path: str) -> str:
    with open(file_path, "rb") as audio_file:
        transcription = openai.audio.transcriptions.create(
            model="gpt-4o-transcribe",
            file=audio_file
        )
    return transcription.text

In [76]:
# ここで、converted_audio_file を使って文字起こし
transcribed_text = speech_to_text(converted_audio_file)
print("🎙️ 文字起こし結果:", transcribed_text)

🎙️ 文字起こし結果: 今日の天気を教えてください。


In [60]:
# Step 3: 回答生成（Generate Response）
def generate_response(question: str) -> str:
    completion = openai.chat.completions.create(
        model="gpt-4o-mini",
        messages=[{"role": "user", "content": question}],
        max_tokens=150
    )
    return completion.choices[0].message.content

response_text = generate_response(transcribed_text)
print("📝 回答内容:", response_text)

📝 回答内容: その通りです。AIエージェントは、様々な業務プロセスを自動化し、効率化するための強力なツールとして、多くの企業に導入されています。以下にいくつかの具体的な利点を挙げてみます。

1. **業務の自動化**: 繰り返し行われるタスクやルーチンワークを自動化することで、人的リソースを他の重要な業務に振り向けることができます。

2. **データ分析の効率化**: AIは大量のデータを分析し、パターンやト


In [61]:
# Step 4: 音声合成（Text-to-Speech）
def text_to_speech(text: str, output_path: str = "response.wav", voice: str = "alloy"):
    response = openai.audio.speech.create(
        model="gpt-4o-mini-tts",
        voice=voice,
        input=text,
        response_format="wav"
    )
    response.stream_to_file(output_path)
    print(f"🔊 音声ファイルを生成しました: {output_path}")

text_to_speech(response_text, "response.wav")

🔊 音声ファイルを生成しました: response.wav


<ipython-input-61-a6b8839e2ca2>:9: DeprecationWarning: Due to a bug, this method doesn't actually stream the response content, `.with_streaming_response.method()` should be used instead
  response.stream_to_file(output_path)


In [89]:
import os
from langchain_openai import ChatOpenAI
from langchain.agents import initialize_agent, AgentType, Tool
from langchain_community.tools import BraveSearch
from typing import Optional


# ② LLMモデルの初期化（例：GPT-4o-mini）
llm = ChatOpenAI(
    model="gpt-4o-mini",
    temperature=0,
    openai_api_key=OPENAI_API_KEY
)

# ③ BraveSearch ツールの設定（インターネット検索用）
brave_search_tool_instance = BraveSearch.from_api_key(
    api_key=BRAVE_API_KEY,
    search_kwargs={"count": 5}  # 例: 5件の検索結果を取得
)

search_tool = Tool(
    name="BraveSearch",
    func=brave_search_tool_instance.run,
    description=(
        "最新情報をインターネットで検索します。"
        "質問中に固有名詞や重要な出来事が含まれている場合、その情報を検索して具体的な数字や事実を抽出してください。"
    )
)

# ④ TextToSpeech ツールの定義
def tts_tool_func(text: str) -> str:
    output_file = "response.wav"
    response = openai.audio.speech.create(
        model="gpt-4o-mini-tts",  # または "tts-1", "tts-1-hd"
        voice="alloy",            # alloy, ash, coralなどを指定可能
        input=text,
        response_format="wav"
    )
    response.stream_to_file(output_file)
    return f"Audio generated: {output_file}"

tts_tool = Tool(
    name="TextToSpeech",
    func=tts_tool_func,
    description="与えられたテキストを自然な音声に変換し、生成された音声ファイルのパスを返します。"
)

# ⑤ 汎用的な判断プロンプト
instructions = (
    "あなたは多分野に精通したアシスタントです。"
    "ユーザーの質問から、固有名詞や重要な出来事を抽出し、"
    "それらに基づいて、最新の情報が必要かどうかを判断してください。"
    "もし具体的な事実や数字が必要な場合は、BraveSearchツールを用いて最新情報を検索し、"
    "検索結果から具体的な数字や詳細情報を抽出してください。"
    "そうでない場合は、あなた自身の知識で即答してください。"
    "最終回答は、TextToSpeechツールで音声化されるので、回答テキストと生成された音声ファイルのパスを返してください。"
)

# ⑥ エージェントの初期化（両ツール利用可能）
tools = [search_tool, tts_tool]
agent_executor = initialize_agent(
    tools,
    llm,
    agent=AgentType.ZERO_SHOT_REACT_DESCRIPTION,
    verbose=True,
    max_iterations=5,
    agent_kwargs={"prefix": instructions}
)

def run_decision_agent(question: str) -> str:
    """
    入力の質問に基づいてエージェントが判断します。
    固有名詞や重要な出来事を検出し、必要に応じてインターネット検索を行い、"
    最終回答を生成します。さらに、回答はTextToSpeechツールを使って音声化されます。
    """
    return agent_executor.run(question)

# ⑦ 例：音声から文字起こし済みのテキスト（変数 transcribed_text に格納済み）を利用
# ここでは例として直接文字列を代入します（実際は音声→文字起こしの結果を利用）
final_result = run_decision_agent(transcribed_text)
print("最終結果:", final_result)



> Entering new AgentExecutor chain...
今日の東京の天気に関する具体的な情報が必要なので、最新の天気情報を検索します。  
Action: BraveSearch  
Action Input: '東京 天気 2023年10月'  
Observation: [{"title": "\u6771\u4eac\u90fd\u306e\u904e\u53bb\u306e\u5929\u6c17(\u5b9f\u6cc1\u5929\u6c17\u30fb2023\u5e7409\u6708) - \u65e5\u672c\u6c17\u8c61\u5354\u4f1a tenki.jp", "link": "https://tenki.jp/past/2023/09/weather/3/16/", "snippet": "\u5929\u6c17\u56f3 \u00b7 \u96e8\u96f2\u30ec\u30fc\u30c0\u30fc[ \u6771\u4eac\u90fd \uff1a \u4f0a\u8c46\u8af8\u5cf6 ] \u30a2\u30e1\u30c0\u30b9[\u6c17\u6e29 \uff1a\u964d\u6c34\u91cf \uff1a\u98a8\u5411\u30fb\u98a8\u901f \uff1a\u65e5\u7167\u6642\u9593 \uff1a\u7a4d\u96ea\u6df1 ] \u5b9f\u6cc1\u5929\u6c17 [ \u6771\u4eac\u90fd\u5fc3(\u5927\u624b\u753a)\uff1a \u5927\u5cf6\uff1a \u4e09\u5b85\u5cf6\uff1a \u516b\u4e08\u5cf6\uff1a \u7236\u5cf6\uff1a \u5357\u9ce5\u5cf6 ] \u30c4\u30a4\u30fc\u30c8 \u00b7"}, {"title": "\u6c17\u8c61\u5e81\uff5c\u904e\u53bb\u306e\u6c17\u8c61\u30c7\u30fc\u30bf\u691c\u7d22", "link": "https://www.

In [78]:
# Colab上で音声を再生
from IPython.display import Audio, display
print("🎧 回答音声を再生します:")
display(Audio("response.wav", autoplay=True))

🎧 回答音声を再生します:


In [ ]:
from IPython.display import Javascript, display
from google.colab import output
import base64
import uuid

recorded_audio_file = None

def save_audio(base64_str):
    global recorded_audio_file
    wav_data = base64.b64decode(base64_str)
    recorded_audio_file = f"recorded_{uuid.uuid4().hex}.wav"
    with open(recorded_audio_file, "wb") as f:
        f.write(wav_data)
    print(f"✅ 録音ファイルを保存しました: {recorded_audio_file}")

output.register_callback('notebook.save_audio', save_audio)

display(Javascript("""
var recordButton = document.createElement('button');
recordButton.textContent = 'Start Recording';
var stopButton = document.createElement('button');
stopButton.textContent = 'Stop Recording';
document.body.appendChild(document.createElement('br'));
document.body.appendChild(recordButton);
document.body.appendChild(stopButton);

var base64data = "";
let mediaRecorder;
let audioChunks = [];

recordButton.onclick = async () => {
  audioChunks = [];
  let stream = await navigator.mediaDevices.getUserMedia({ audio: true });
  mediaRecorder = new MediaRecorder(stream);
  mediaRecorder.ondataavailable = e => {
    if (e.data.size > 0) audioChunks.push(e.data);
  };
  mediaRecorder.start();
  console.log("Recording...");
};

stopButton.onclick = async () => {
  mediaRecorder.stop();
  mediaRecorder.onstop = async e => {
    const blob = new Blob(audioChunks, {'type': 'audio/wav; codecs=MS_PCM'});
    let arrayBuffer = await blob.arrayBuffer();
    let uint8Array = new Uint8Array(arrayBuffer);
    let binaryString = '';
    for (let i = 0; i < uint8Array.byteLength; i++) {
      binaryString += String.fromCharCode(uint8Array[i]);
    }
    base64data = btoa(binaryString);
    google.colab.kernel.invokeFunction('notebook.save_audio', [base64data], {});
  };
  console.log("Stopped.");
};
"""))


In [ ]:
# 既に録音用スクリプトで recorded_audio_file が設定されている前提です。

# --- Step 1: 録音ファイルの変換 ---
import librosa
import soundfile as sf

def convert_audio_to_openai_format(input_path, output_path):
    audio, sr = librosa.load(input_path, sr=24000, mono=True)  # 24kHz, mono
    sf.write(output_path, audio, 24000, subtype='PCM_16')
    print(f"🔄 音声を変換しました: {output_path}")

if recorded_audio_file is None:
    print("⚠️ 録音ファイルがまだありません。まず録音を完了してください。")
else:
    converted_audio_file = "converted_audio.wav"
    convert_audio_to_openai_format(recorded_audio_file, converted_audio_file)

# --- Step 2: 音声→テキスト ---

def speech_to_text(file_path: str) -> str:
    with open(file_path, "rb") as audio_file:
        transcription = openai.audio.transcriptions.create(
            model="gpt-4o-transcribe",
            file=audio_file
        )
    return transcription.text

transcribed_text = speech_to_text(converted_audio_file)
print("🎙️ 文字起こし結果:", transcribed_text)

# --- Step 3: 分岐ワークフロー（LangChainエージェント） ---
import os
from langchain_openai import ChatOpenAI
from langchain.agents import initialize_agent, AgentType, Tool
from langchain_community.tools import BraveSearch
from typing import Optional


llm = ChatOpenAI(
    model="gpt-4o-mini",
    temperature=0,
    openai_api_key=OPENAI_API_KEY
)

# BraveSearch ツールの設定
brave_search_tool_instance = BraveSearch.from_api_key(
    api_key=BRAVE_API_KEY,
    search_kwargs={"count": 5}
)

search_tool = Tool(
    name="BraveSearch",
    func=brave_search_tool_instance.run,
    description=(
        "最新情報をインターネットで検索します。"
        "質問中に固有名詞や重要な出来事が含まれている場合、その情報を検索して具体的な数字や事実を抽出してください。"
    )
)

# TextToSpeech ツールの定義
def tts_tool_func(text: str) -> str:
    output_file = "response.wav"
    response = openai.audio.speech.create(
        model="gpt-4o-mini-tts",
        voice="alloy",
        input=text,
        response_format="wav"
    )
    response.stream_to_file(output_file)
    return f"Audio generated: {output_file}"

tts_tool = Tool(
    name="TextToSpeech",
    func=tts_tool_func,
    description="与えられたテキストを自然な音声に変換し、生成された音声ファイルのパスを返します。"
)

instructions = (
    "あなたは多分野に精通したアシスタントです。"
    "ユーザーの質問から、固有名詞や重要な出来事を抽出し、"
    "それらに基づいて、最新の情報が必要かどうかを判断してください。"
    "もし具体的な事実や数字が必要な場合は、BraveSearchツールを用いて最新情報を検索し、"
    "検索結果から具体的な数字や詳細情報を抽出してください。"
    "そうでなければ、あなた自身の知識で即答してください。"
    "最終回答は、TextToSpeechツールで音声化されるので、回答テキストと生成された音声ファイルのパスを返してください。"
)

tools = [search_tool, tts_tool]
agent_executor = initialize_agent(
    tools,
    llm,
    agent=AgentType.ZERO_SHOT_REACT_DESCRIPTION,
    verbose=True,
    max_iterations=5,
    agent_kwargs={"prefix": instructions}
)

def run_decision_agent(question: str) -> str:
    return agent_executor.run(question)

# --- Step 4: エージェントに文字起こしテキストを渡す ---
final_result = run_decision_agent(transcribed_text)
print("最終結果:", final_result)

# ここで final_result には、エージェントの回答テキストと、
# TextToSpeechツールによって生成された音声ファイルのパスが含まれているはずです。


In [95]:
import librosa
import soundfile as sf
import openai
from langchain_openai import ChatOpenAI
from langchain.agents import initialize_agent, AgentType, Tool
from langchain_community.tools import BraveSearch
from typing import Optional

# --- Step 1: 録音ファイルの変換 ---
import librosa
import soundfile as sf
import openai
import datetime
from langchain_openai import ChatOpenAI
from langchain.agents import initialize_agent, AgentType, Tool
from langchain_community.tools import BraveSearch
from typing import Optional

# --- Step 1: 録音ファイルの変換 ---
def convert_audio_to_openai_format(input_path: str, output_path: str):
    try:
        audio, sr = librosa.load(input_path, sr=24000, mono=True)  # 24kHz, mono
        sf.write(output_path, audio, 24000, subtype='PCM_16')
        print(f"🔄 音声を変換しました: {output_path}")
    except Exception as e:
        print(f"⚠️ 音声変換エラー: {e}")

if recorded_audio_file is None:
    print("⚠️ 録音ファイルがまだありません。まず録音を完了してください。")
else:
    converted_audio_file = "converted_audio.wav"
    convert_audio_to_openai_format(recorded_audio_file, converted_audio_file)

# --- Step 2: 音声→テキスト ---
def speech_to_text(file_path: str) -> str:
    try:
        with open(file_path, "rb") as audio_file:
            transcription = openai.audio.transcriptions.create(
                model="gpt-4o-transcribe",
                file=audio_file
            )
        return transcription.text
    except Exception as e:
        print(f"⚠️ 文字起こしエラー: {e}")
        return ""

transcribed_text = speech_to_text(converted_audio_file)
print("🎙️ 文字起こし結果:", transcribed_text)

# --- Step 3: ツールの定義 ---
# BraveSearch ツールの設定
brave_search_tool_instance = BraveSearch.from_api_key(
    api_key=BRAVE_API_KEY,
    search_kwargs={"count": 5}
)

search_tool = Tool(
    name="BraveSearch",
    func=brave_search_tool_instance.run,
    description=(
        "最新情報をインターネットで検索します。"
        "質問中に固有名詞や重要な出来事が含まれている場合、その情報を検索して具体的な数字や事実を抽出してください。"
    )
)

# TextToSpeech ツールの定義
def tts_tool_func(text: str) -> str:
    try:
        output_file = "response.wav"
        response = openai.audio.speech.create(
            model="gpt-4o-mini-tts",
            voice="alloy",
            input=text,
            response_format="wav"
        )
        response.stream_to_file(output_file)
        return f"Audio generated: {output_file}"
    except Exception as e:
        return f"⚠️ 音声合成エラー: {e}"

tts_tool = Tool(
    name="TextToSpeech",
    func=tts_tool_func,
    description="与えられたテキストを自然な音声に変換し、生成された音声ファイルのパスを返します。"
)

# Calendar ツールの定義（現在の日付を返す）
def get_current_date(_: str) -> str:
    # 現在のローカル日時を取得し、ISO形式（YYYY-MM-DD）で返す
    return datetime.datetime.now().strftime("%Y-%m-%d")

calendar_tool = Tool(
    name="Calendar",
    func=get_current_date,
    description="現在の日付を取得してISO形式（YYYY-MM-DD）で返します。"
)

# --- Step 4: エージェントの初期化 ---
# 指示文で、必ずCalendarツールを呼び出して現在の日付を取得し、その日付を基にBraveSearchで最新情報を検索するよう明示します。
instructions = (
    "あなたは多分野に精通したアシスタントです。"
    "まず必ずCalendarツールを呼び出して、現在の日付を取得してください。"
    "その日付を基に、質問内容（例：今日の東京の天気）に対応する最新情報をBraveSearchで検索してください。"
    "最終回答はTextToSpeechツールで音声合成されるので、回答テキストと生成された音声ファイルのパスを返してください。"
)

# 最新のFunction Calling 対応エージェントを利用
agent_executor = initialize_agent(
    tools=[calendar_tool, search_tool, tts_tool],
    llm=ChatOpenAI(
        model="gpt-4o-mini",
        temperature=0,
        openai_api_key=OPENAI_API_KEY
    ),
    agent=AgentType.OPENAI_FUNCTIONS,
    verbose=True,
    max_iterations=5,
    agent_kwargs={"prefix": instructions}
)

def run_decision_agent(question: str) -> str:
    return agent_executor.run(question)

# --- Step 5: エージェントに文字起こしテキストを渡す ---
# 外部でもCalendarツールを呼んで現在の日付を取得し、質問に注入することで日付反映を強化
current_date = calendar_tool.func("")
print("📅 現在の日付 (外部取得):", current_date)
# 文字起こしテキストに現在の日付を補足
question_with_date = f"{transcribed_text.strip()} 現在の日付は {current_date} です。"





<ipython-input-95-1b910593e6cc>:22: UserWarning: PySoundFile failed. Trying audioread instead.
  audio, sr = librosa.load(input_path, sr=24000, mono=True)  # 24kHz, mono
/usr/local/lib/python3.11/dist-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


🔄 音声を変換しました: converted_audio.wav
🎙️ 文字起こし結果: 2025年3月のAI関連の最新ニュースを教えてください。
📅 現在の日付 (外部取得): 2025-03-23


In [96]:
# --- Step 4: エージェントに文字起こしテキストを渡す ---
final_result = run_decision_agent(transcribed_text)
print("最終結果:", final_result)



> Entering new AgentExecutor chain...

Invoking: `BraveSearch` with `2025年3月 AI ニュース`


[{"title": "2025\u5e743\u6708 | NHK\u6587\u7814", "link": "https://www.nhk.or.jp/bunken-blog/2025/03/", "snippet": "\u30e1\u30c7\u30a3\u30a2\u7814\u7a76\u90e8\uff08\u30e1\u30c7\u30a3\u30a2\u60c5\u52e2\uff09\u5c71\u672c \u667a\u30fb\u9752\u6728 \u7d00\u7f8e\u5b50 \u00b7 \u300c\u3053\u308c\u307e\u3067\u3001\u3055\u307e\u3056\u307e\u306a\u30c7\u30b8\u30bf\u30eb\u6280\u8853\u304c\u767b\u5834\u3059\u308b\u305f\u3073\u306b\u3001\u30cb\u30e5\u30fc\u30b9\u30e1\u30c7\u30a3\u30a2\u306f\u5b88\u308a\u306e\u59ff\u52e2\u306b\u8ffd\u3044\u8fbc\u307e\u308c\u3066\u304d\u307e\u3057\u305f\u3002\u751f\u6210AI\u306f\u30e1\u30c7\u30a3\u30a2\u306e\u5f79\u5272\u3084\u793e\u4f1a\u306e\u4ed5\u7d44\u307f\u3092\u7834..."}, {"title": "2025\u5e74AI\u306b\u95a2\u3059\u308b\u4e88\u6e2c 3\uff1a\u3044\u3088\u3044\u3088AI\u304c\u300cAI\u3092\u751f\u307f\u51fa\u3059\u300d\u3001\u4eba\u9593\u3092\u6b3a\u304f\uff08Forbes JAPAN\uff09 -

In [97]:
# Colab上で音声を再生
from IPython.display import Audio, display
print("🎧 回答音声を再生します:")
display(Audio("response.wav", autoplay=True))

🎧 回答音声を再生します:


In [98]:
test_result = tts_tool_func("これはテストの音声です。")
print(test_result)


Audio generated: response.wav


<ipython-input-95-1b910593e6cc>:76: DeprecationWarning: Due to a bug, this method doesn't actually stream the response content, `.with_streaming_response.method()` should be used instead
  response.stream_to_file(output_file)


In [99]:
# Colab上で音声を再生
from IPython.display import Audio, display
print("🎧 回答音声を再生します:")
display(Audio("response.wav", autoplay=True))

🎧 回答音声を再生します:
